# GRAIN DECOMPOSITION AND RECOMPOSITION USING SPHERICAL HARMONICS
This Jupyter notebook illustrates the processes of decomposition and recomposition of grains using spherical harmonics.

This procedure allows to represent anallitically every barley grain to later recompose it using a uniform domain, so the whole dataset has the same number of vertices and faces. This common domain creates new ways of treating this kind of 3D data (meshes). For example, it is possible to compute sums, averages, errors, deviations (and more) of grains.

From now on, sometimes we will write SH instead of spherical harmonics to compact explanations.

### IMPORTS

In [1]:
import numpy as np
import trimesh
import scipy
import os
import matplotlib.pyplot as plt
import pickle
import trimesh
from copy import deepcopy
from math import floor, sqrt

from scipy.interpolate import griddata
from scipy.special import sph_harm

from tqdm import trange, tqdm

The objective of decomposing a grain into spherical harmonics is being able to represent it independently of the number of points or faces of the mesh.

To use this procedure let's consider the grain surface, given as a point cloud, a sample of a continuous function defined on a sphere. Once this consideration is made, the remaining steps, and the functions we will use, focus on calculating the coefficients of the decomposition, which involve a double integral.

Let $f(\theta,\varphi)$ be the barley grain surface and $Y^{m}_l:S^2 \rightarrow\mathbb{R}$ the real (not complex) orthonormal basis of spherical harmonics, then $f$ can be expanded as the sum 
$$f(\theta,\varphi)=\sum_{l=0}^{\infty}\sum_{m=-l}^{l}f^m_lY^m_l(\theta,\varphi)$$
where

$$f^m_l=\int_{\Omega}f(\theta,\varphi)Y^m_l(\theta,\varphi)d\Omega = \int_{0}^{2\pi}d\varphi\int_{0}^{\pi}d\theta sin(\theta)f(\theta,\varphi)Y^m_l(\theta,\varphi)$$

### Functions

- cartesian_coordinates_3d and spherical_coordinates function: switch between spherical and cartesian coordinates.
- real_spherical_harmonic: evaluate the real spherical harmonic $Y^m_l$ given $\theta$ and $\phi$ as the corresponding theta and phi arrays.
- simpson_integral_grids: computes the double integral of a function using the Composite Simpson's rule
- compute_grids: computes theta and phi grids and interpolates the value of $f$ for this grids given the point cloud.
- coefficient: computes a SH coefficient $f^m_l$ using r, phi and theta grids.
- spherical_coefficients: computes all SH coefficients from $l=0$ to $l\_max$.
- compute_coefficients_from_mesh: given a mesh and a maximum l value $l\_max$, computes all SH coefficients calling the previous functions.


In [6]:
# --------- Coordinate systems ---------
def cartesian_coordinates_3d(r, phi, theta):
    """
    Convert spherical coordinates (r, phi, theta) to Cartesian coordinates (x, y, z).

    Parameters:
    -----------
    r : np.array
        Array of radial distances.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].

    Returns:
    --------
    x : np.array
        Array of x-coordinates.
    y : np.array
        Array of y-coordinates.
    z : np.array
        Array of z-coordinates.
    """
    x = r * np.sin(theta) * np.cos(phi)
    y = r * np.sin(theta) * np.sin(phi)
    z = r * np.cos(theta)
    return x, y, z

def spherical_coordinates(x, y, z):
    """
    Converts Cartesian coordinates (x, y, z) to spherical coordinates (r, phi, theta).

    Parameters:
    -----------
    x : np.array
        Array of x-coordinates.
    y : np.array
        Array of y-coordinates.
    z : np.array
        Array of z-coordinates.

    Returns:
    --------
    r : np.array
        Array of radial distances.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].
    """
    r = np.sqrt(x**2+y**2+z**2)
    theta = np.arctan2(np.sqrt(x**2+y**2), z)
    phi = np.arctan2(y, x)
    
    theta[theta < 0] += 2*np.pi
    phi[phi < 0] += 2*np.pi
    
    return r, phi, theta

def spherical_coordinates_from_mesh(mesh):
    """
    Convert mesh vertices to spherical coordinates.

    Parameters:
    -----------
    mesh : trimesh.base.Trimesh
        Mesh object.

    Returns:
    --------
    r : np.array
        Array of radial distances.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].
    """
    x = mesh.vertices[:, 0]
    y = mesh.vertices[:, 1]
    z = mesh.vertices[:, 2]
    
    return spherical_coordinates(x, y, z)

def update_vertices_with_spherical_coordinates(r, phi, theta, mesh):
    """
    Update mesh vertices with new Cartesian coordinates computed from spherical coordinates.

    Parameters:
    -----------
    r : np.array
        Array of radial distances.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].
    mesh : trimesh.base.Trimesh
        Mesh object.

    Returns:
    --------
    None
    """
    x, y, z = cartesian_coordinates_3d(r, phi, theta)
    mesh.vertices = np.column_stack((x, y, z))

# --------- Spherical harmonic computation ---------
def real_spherical_harmonic(m, l, phi, theta):
    """
    Compute the real spherical harmonic function for given degree and order.

    Parameters:
    -----------
    m : int
        Order of the spherical harmonic.
    l : int
        Degree of the spherical harmonic.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].

    Returns:
    --------
    np.array
        Array of real spherical harmonic values.

    Notes:
    ------
    This function computes real spherical harmonic values from scipy.special.sph_harm function of
    the scipy module, which returns complex spherical harmonics. Real harmonics don't have a
    function in the scipy module but admits a representation using complex harmonics.
    Also, NaN values may be produced for l values above 85.
    """
    assert np.abs(m) <= l
    if m == 0:
        return np.real(scipy.special.sph_harm(m, l, phi, theta))
    elif m > 0:
        return np.real((1/np.sqrt(2))*(scipy.special.sph_harm(m, l, phi, theta)
                        + ((-1)**m) * scipy.special.sph_harm(-m, l, phi, theta)))
    elif m < 0:
        return np.real((1/(1j*np.sqrt(2)))*(scipy.special.sph_harm(-m, l, phi, theta)
                            - ((-1)**(-m)) * scipy.special.sph_harm(m, l, phi, theta)))

def simpson_integral_grids(x_grid, y_grid, eval_grid):
    """
    Compute the Simpson's rule numerical integration over 2D grids.

    Parameters:
    -----------
    x_grid : np.array
        Grid of x-coordinates.
    y_grid : np.array
        Grid of y-coordinates.
    eval_grid : np.array
        Grid of values to be integrated.

    Returns:
    --------
    float
        Result of the Simpson's rule integration.

    Notes:
    ------
    ERRORS AND COMPACTNESS
    """
    n = int(x_grid.shape[0]/2)
    m = int(y_grid.shape[1]/2)

    h = (x_grid[0,-1] - x_grid[0,0]) / (2*n)    
    hx = (y_grid[-1,0] - y_grid[0,0]) / (2*m)

    # Edges
    J1 =  np.sum(eval_grid[[0,2*n], [0,-1]]) + \
        2*np.sum(eval_grid[[0,2*n], 2:2*m:2]) + \
        4*np.sum(eval_grid[[0,2*n], 1:2*m:2])
    
    # Even values
    J2 =  np.sum(eval_grid[2:2*n:2, [0,-1]]) +  \
        2*np.sum(eval_grid[2:2*n:2, 2:2*m:2]) + \
        4*np.sum(eval_grid[2:2*n:2, 1:2*m:2])
    J3 = np.sum(eval_grid[1:2*n:2, [0,-1]]) + 2*np.sum(eval_grid[1:2*n:2, 2:2*m:2]) + 4*np.sum(eval_grid[1:2*n:2, 1:2*m:2])

    return (J1 + 2*J2 + 4*J3)*h*hx/9

def compute_grids(r, phi, theta, shape = (201,201)):
    """
    Compute grids of radial, azimuthal, and zenith coordinates.

    Parameters:
    -----------
    r : np.array
        Array of radial distances.
    phi : np.array
        Array of azimuthal angles in the range [0, 2*pi].
    theta : np.array
        Array of zenith angles in the range [0, pi].
    shape : tuple, optional
        Shape of the resulting grids. Default is (201, 201).

    Returns:
    --------
    r_grid : np.array
        Grid of radial distances.
    phi_grid : np.array
        Grid of azimuthal angles.
    theta_grid : np.array
        Grid of zenith angles.

    Notes:
    ------
    The method used to interpolate r in a grid is getting the nearest value.
    """
    n_phi, n_theta = shape
    p = np.linspace(0, 2*np.pi, n_phi)
    t = np.linspace(0, np.pi, n_theta)

    phi_grid, theta_grid = np.meshgrid(p, t) # phi over cols, theta over rows
    # griddata((points), values, (Points at which to interpolate data))
    r_grid = griddata((phi, theta), r, (phi_grid, theta_grid), method='nearest', fill_value=0.0)
    return r_grid, phi_grid, theta_grid

def coefficient(m, l, phi_grid, theta_grid, r_grid):
    eval_grid = r_grid * np.sin(theta_grid) * real_spherical_harmonic(m, l, phi_grid, theta_grid)
    return simpson_integral_grids(phi_grid, theta_grid, eval_grid)

def spherical_coefficients(max_l, phi_grid, theta_grid, r_grid, progress_bar=False):
    coefficients = []
    indices = range((max_l+1)**2)
    if progress_bar:
        indices = tqdm(indices, dynamic_ncols=True)
    for index in indices:
        l = floor(sqrt(index))
        m = index - l - l**2
        coefficients.append(coefficient(m, l, phi_grid, theta_grid, r_grid))
    return coefficients

def compute_coefficients_from_mesh(mesh, max_l, shape = (201, 201), progress_bar=False):
    r, phi, theta = spherical_coordinates_from_mesh(mesh)
    r_grid, phi_grid, theta_grid = compute_grids(r, phi, theta, shape = shape)

    coefs = spherical_coefficients(max_l, phi_grid, theta_grid, r_grid, progress_bar=progress_bar)
    return coefs

def spherical_harmonic(l, m, radius=5, resolution=50):
    """
    Generate a mesh representing a specific spherical harmonic.

    Parameters:
    -----------
    l : int
        Degree of the spherical harmonic.
    m : int
        Order of the spherical harmonic.
    radius : float, optional
        Radius of the spherical mesh. Default is 5.
    resolution : int, optional
        Resolution of the spherical mesh. Default is 50.

    Returns:
    --------
    trimesh.base.Trimesh
        Mesh representing the specified spherical harmonic.

    Notes:
    ------
    Negative values of the spherical harmonic cannot be represented as a radius, so the resulting
    mesh is computed from the absolut value of the radius.
    """
    # Spherical mesh to use as a base
    sphere_mesh = trimesh.creation.uv_sphere(radius=radius, count=[resolution, resolution])
    
    # Transformation into spherical coordinates
    _, phi, theta = spherical_coordinates_from_mesh(sphere_mesh)
    
    # Compute new radius as the absolut value of the harmonic
    r_new = np.zeros(phi.shape)
    r_new += np.abs(real_spherical_harmonic(m, l, phi, theta))
    
    # Recompose the new radius into cartesian coordinates        
    update_vertices_with_spherical_coordinates(r_new, phi, theta, sphere_mesh)
    
    return sphere_mesh

def print_coefficients(coefficients):
    print("Coeficients (l,m)")
    max_l = int(np.sqrt(len(coefficients))) - 1
    cont = 0
    longitud_maxima_coeficientes = max(len("{:.3f}".format(x)) for x in coefficients)
    longitud_maxima_valores = max(len(f"({l},{m})") for l in range(0, max_l) for m in range(-l, l + 1))
    for l in range(0, max_l + 1):
        for m in range(-l, l + 1):
            print("{:>{}}:".format(f"({l},{m})", longitud_maxima_valores), end=" ")
            print("{:>{}}".format("{:.3f}".format(coefficients[cont]), longitud_maxima_coeficientes), end=", ")
            cont += 1
        print("")

# --------- Grain reconstruction ---------
def tesselation_into_grain(coefficients, tesselation, phi=None, theta=None, progress_bar=False):
    """
    Creates a mesh based on a given tesselation preserving the number of faces and
    vertices applying the SH decomposition on every vertex.
    
    Parameters:
    -----------
    coefficients : array-like
        Coefficients of the spherical harmonic expansion.
    tesselation : str or trimesh.base.Trimesh
        If str, it represents the path to the mesh file. If trimesh.base.Trimesh,
        it represents the mesh object itself.
    phi : array-like, optional
        Phi values (azimutal angle) in radians for each vertex of the tesselation mesh.
        If not provided, they are computed from the mesh vertices.
    theta : array-like, optional
        Theta values (polar angle) in radians for each vertex of the tesselation mesh.
        If not provided, they are computed from the mesh vertices.
    progress_bar : bool, optional
        If True, a progress bar will be displayed during computation
        
    Returns:
    --------
    trimesh.base.Trimesh
        The tesselation mesh with the updated vertices according to the the spherical
        harmonic expansion coefficients.
    
    Notes:
    ------
    Deformation is computed in spherical coordinates and transformed back to Cartesian.
    """
    # Checking if tesselation is a path or a mesh
    if isinstance(tesselation, str):
        tesselation_mesh = trimesh.load(tesselation)
    elif isinstance(tesselation, trimesh.base.Trimesh):
        tesselation_mesh = deepcopy(tesselation)
    
    # Compute phi and theta values if not given
    if not phi or not theta:
        _, phi, theta = spherical_coordinates_from_mesh(tesselation_mesh)
    
    # Accumulate values in r_new
    r_new = np.zeros(phi.shape)
    max_l = round(sqrt(len(coefficients))) - 1
    indices = range((max_l+1)**2)
    
    # Progress bar to show the remaining time
    if progress_bar:
        indices = tqdm(indices, dynamic_ncols=True)
    
    # Iterate over coefficients and add the result on the new radius r_new
    for index in indices:
        l = floor(sqrt(index))
        m = index - l - l**2
        if not np.isnan(coefficients[index]):
            r_new += coefficients[index] * real_spherical_harmonic(m, l, phi, theta)
        else:
            print(f"Reaching NaN values evaluating scipy.special.sph_harm at l={l}, m={m}")
    
    # Recompose the new radius into cartesian coordinates        
    update_vertices_with_spherical_coordinates(r_new, phi, theta, tesselation_mesh)
    return tesselation_mesh

def tesselation_into_dataset(dataset_path, tesselation_path, destination_path=None):
    """
    Reconstructs a whole dataset using a precomputed tesselation.

    Parameters:
    -----------
    dataset_path : str
        Path to the folder containing the dataset.
    tesselation_path : str
        Path to the precomputed tesselation mesh.
    destination_path : str, optional
        Path to the folder where the reconstructed dataset will be saved. If None, a defualt name will be set.
    Returns:
    --------
    None

    Notes:
    ------
    This function reconstructs meshes for each item in the dataset located
    at `dataset_path` using a precomputed tesselation mesh provided at `tesselation_path`.
    It calculates the values of phi and theta to avoid recalculating them on each call to
    `tesselation_into_grain`. The deformed meshes are saved in a folder structure mirroring
    the original dataset structure, with the reconstructed meshes replacing the original ones.
    Items that are not stl files or directories will be ignored, so they won't appear in the
    new dataset.
    """
    # Default name for the new dataset
    if not destination_path:
        destination_path = f"{folder_path}_RECONSTRUCTED"
    
    #print(f"Entering the folder {dataset_path}")
    # Get current folder contents
    paths = os.listdir(dataset_path)
    paths.sort()
    
    # Compute the values ​​of phi and theta to avoid recalculating them on each call to tesselation_into_grain
    tesselation_mesh = trimesh.load(tesselation_path)
    _, phi, theta = spherical_coordinates_from_mesh(tesselation_mesh)
    
    # For every content in the current folder
    for path in paths:
        # Updating paths to clone the original folder hierarchy
        import_path = dataset_path + "/" + path
        export_path = destination_path + "/" + path
        
        # Checking if it has already been constructed
        if not os.path.exists(export_path[:-4]):  # [:-4] to remove .pkl extension
            # Load coefficients
            with open(import_path, 'rb') as archivo:
                coefficients = pickle.load(archivo)
            # Compute new mesh
            mesh = tesselation_into_grain(tesselation_mesh, phi, theta, coefficients, progress_bar=False)
            # Export mesh
            os.makedirs(destination_path, exist_ok=True)
            mesh.export(export_path[:-4])  # [:-4] to remove .pkl extension
        
        # Recursion over directories
        elif os.path.isdir(import_path):
            tesselation_into_dataset(import_path, tesselation_path, destination_path=export_path)

Before starting to decompose grains, let's plot some harmonics.

Note that these harmonics are functions with positive and negative values. If we try to represent this function as a sphere radius, the negative values won't be represented or even raise exceptions. So for visualization purposes, we will plot the absolut value of the harmonics instead their real values.

In [7]:
spherical_harmonic(l=2, m=1, resolution=200).show()

In [8]:
spherical_harmonic(l=5, m=3, resolution=200).show()

In [ ]:
spherical_harmonic(l=6, m=0, resolution=200).show()

Let's first load and show a mesh.

In [ ]:
# Load mesh
data_dir = "./data/"
mesh_path = data_dir + "unoriented_dataset_ORIENTED/Dundee/2ROW British/DHBT16P103 2.stl"
mesh = trimesh.load(mesh_path)
mesh.show()

Notice that there are harmonics for any value $l\in\mathbb{N}\cup\{0\}$ and $m\in[-l,l]$. We will compute all coefficients $\forall m$ from $l=0$ to $l\_max$. Technically, the higher $l\_max$ value, the greater approximation of the grain, but due to error propagation and finite representation, a very high $l\_max$ produces rugosity (proved later in this notebook).

Also notice that the number of coefficients for a given $l\_max$ value is $(l\_max + 1)^2 = \sum_{l=0}^{l\_max}(2l + 1)$, so if we compute all coefficients up to $l\_max=50$, we can reduce the precision of the representation as much as we want by choosing a subarray.

Let's see how this precision varies computing coefficients for a value of $l\_max=100$. This will take a few minuts (~15-20) for new grains, but for this one we can load them from a pickle file.

Sometimes the function scipy.special.sph_harm used to evaluate sphercial harmonics produces NaNs for values of $l$ above 85, so the representation should not exceed $l\_max=85$.

In [ ]:
coefficients_path = data_dir + "coefficients_100.pkl"
if os.path.exists(coefficients_path):
    with open(coefficients_path, 'rb') as coefficients_file:
        coefficients_100 = pickle.load(coefficients_file)
else:
    coefficients_100 = compute_coefficients_from_mesh(mesh, max_l=100, progress_bar=True)
    with open(coefficients_path, "wb") as coefficients_file:
        pickle.dump(coefficients_100, coefficients_file)

coefficients_85 = coefficients_100[:86**2]
coefficients_70 = coefficients_100[:71**2]
coefficients_50 = coefficients_100[:51**2]
coefficients_30 = coefficients_100[:31**2]
coefficients_15 = coefficients_100[:16**2]
coefficients_5 = coefficients_100[:6**2]

print_coefficients(coefficients_5)

In [ ]:
def load_or_reconstruct(mesh_name, data_dir, coefficients, tesselation_path):
    reconstructed_mesh_path = data_dir + mesh_name
    if os.path.exists(reconstructed_mesh_path):
        mesh = trimesh.load(reconstructed_mesh_path)
    else:
        mesh = tesselation_into_grain(coefficients, tesselation=tesselation_path, phi=None, theta=None, progress_bar=True)
        mesh.export(reconstructed_mesh_path)
    return mesh

In [ ]:
mesh_5 = load_or_reconstruct("mesh_5.stl", data_dir, coefficients_5, mesh_path)
mesh_5.show()

In [ ]:
mesh_15 = load_or_reconstruct("mesh_15.stl", data_dir, coefficients_15, mesh_path)
mesh_15.show()

In [ ]:
mesh_30 = load_or_reconstruct("mesh_30.stl", data_dir, coefficients_30, mesh_path)
mesh_30.show()

In [ ]:
mesh_50 = load_or_reconstruct("mesh_50.stl", data_dir, coefficients_50, mesh_path)
mesh_50.show()

In [ ]:
mesh_70 = load_or_reconstruct("mesh_70.stl", data_dir, coefficients_70, mesh_path)
mesh_70.show()

In [ ]:
mesh_85 = load_or_reconstruct("mesh_85.stl", data_dir, coefficients_85, mesh_path)
mesh_85.show()

If these reconstructions weren't computed before, they would have taken the following time to create them:
|  $l\_max$      | time              |
|:--------------:|:-----------------:|
| 5              | <1s               |
| 15             | 4s                |
| 30             | 20s               |
| 50             | 2m                |
| 70             | 4m                |
| 85             | 6m                |

As can be seen, $l\_max=50$ seems the original grain. For higher values such as $l\_max=85$ there's a rugosity in the grain surface produced by aproximation errors and finite representation. Remark that the grain size in bytes is independent of $l\_max$, this choice only affects the computing time and the precision of the approximation, so maybe there's a better choice than $l\_max=50$.

## UNIFORM DOMAIN RECONSTRUCTION

As we have seen in this notebook, now we are able to reconstruct grains using its decomposition in SH, which is independent of the number of vertices and faces they had before. In the example we've seen, the original grain has been used as a base to reconstruct the grain, but should we use this one to reconstruct the others? We could use a spherical base, but the problem is that the vertices density of the reconstructed grain will be lower at the edges over x axis. 

It's better to use a grain base related to lots of different grains, like the average grain. The problem is computing this average grain if we still don't have a common domain. So the first step is to reconstruct the dataset with a spherical mesh and then compute the average grain. Next, we open this average grain on MeshLab and compute a base with its vertices uniformly distributed (explained later). Finally, we reassemble the whole dataset with this base, achieving a common domain for all grains and being able to operate vertex to vertex.

In [ ]:
def tesselation_into_grain_xyz(tesselation_mesh, phi, theta, coefficients):
    r_new = np.zeros(tesselation_mesh.vertices.shape[0])
    max_l = int(np.rint(np.sqrt(len(coefficients))))
    i = 0
    for l in range(max_l):
        for m in range(-l, l + 1):
            if not np.isnan(coefficients[i]):
                r_new += coefficients[i] * real_spherical_harmonic(m, l, phi, theta)
            i += 1
            
    xx, yy, zz = cartesian_coordinates_3d_xyz(r_new, phi, theta)
    tesselation_mesh.vertices = np.column_stack((xx, yy, zz))
    return tesselation_mesh

In [ ]:
tesselation_path = "../../../data/tesselations/"